In [3]:
import json
import os
from pprint import pprint
import re
from tqdm import tqdm
import random

import uuid
import openai
from openai import OpenAI
import tiktoken
import json
import numpy as np
import requests
from scipy import sparse
#from rank_bm25 import BM25Okapi
#import jieba
from http import HTTPStatus


from concurrent.futures import ThreadPoolExecutor, as_completed
from loguru import logger
import json
import time
from tqdm import tqdm

from rag import get_few_shot

2024-09-06 23:37:23,077 - modelscope - WARNING - Model revision not specified, use revision: v0.0.2


In [4]:
logger.remove()  # 移除默认的控制台输出
logger.add("logs/app_{time:YYYY-MM-DD}.log", level="INFO", rotation="00:00", retention="10 days", compression="zip")
# python -m vllm.entrypoints.openai.api_server --model ./models/Meta-Llama-3.1-8B-Instruct-lora  --served-model-name Meta-Llama-3.1-8B-Instruct-lora --max-model-len=4096
MODEL_NAME = 'Meta-Llama-3.1-8B-Instruct-lora'
def api_retry(MODEL_NAME, query):
    max_retries = 5
    retry_delay = 60  # in seconds
    attempts = 0
    while attempts < max_retries:
        try:
            return call_qwen_api(MODEL_NAME, query)
        except Exception as e:
            attempts += 1   
            if attempts < max_retries:
                logger.warning(f"Attempt {attempts} failed for text: {query}. Retrying in {retry_delay} seconds...")
                time.sleep(retry_delay)
            else:
                logger.error(f"All {max_retries} attempts failed for text: {query}. Error: {e}")
                raise
def call_qwen_api(MODEL_NAME, query):
    # 这里采用dashscope的api调用模型推理，通过http传输的json封装返回结果

    client = OpenAI(
        base_url="http://localhost:8000/v1",
        api_key="sk-xxx", # 随便填写，只是为了通过接口参数校验
    )
    completion = client.chat.completions.create(
      model=MODEL_NAME,
      messages=[
                # {'role':'system','content':'你是一个解决推理任务的专家，你需要分析出问题中的每个实体以及响应关系。然后根据问题一步步推理出结果。并且给出正确的结论。'},

        {"role": "user", "content": query}
      ]
    )
    return completion.choices[0].message.content

# 这里定义了prompt推理模版

def get_prompt(problem, question, options):

    options = '\n'.join(f"{'ABCDEFG'[i]}. {o}" for i, o in enumerate(options))
    
    query = f"""
### 题目:
{problem}
### 问题:
{question}
### 选项：
{options}
"""
    fewshot = get_few_shot(query)
    #fewshot = ''
    prompt = f"""你是一个逻辑推理专家，擅长解决逻辑推理问题。以下是一个逻辑推理的题目，形式为单项选择题。所有的问题都是（close-world assumption）闭世界假设，即未观测事实都为假。请逐步分析问题并在最后一行输出答案，最后一行的格式为"答案是：A"。题目如下：
{fewshot}{query}
### 回答：
"""
    # print(prompt)
    return prompt


# 这里使用extract抽取模获得抽取的结果

def extract(input_text):
    # 正则表达式匹配“答案是：”后面的第一个字符
    #print("input_text is", input_text)
    ans_pattern = re.compile(r"答案是：([A-Za-z0-9])")

    match = ans_pattern.search(input_text)
    #print("match.group(1)", match.group(1))
    if not match:
        return 'Error'

    return match.group(1)


def most_frequent_char(char1, char2, char3):
    # 创建一个字典来存储每个字符的出现次数
    frequency = {char1: 0, char2: 0, char3: 0}
    
    # 增加每个字符的出现次数
    frequency[char1] += 1
    frequency[char2] += 1
    frequency[char3] += 1
    
    # 找到出现次数最多的字符
    most_frequent = max(frequency, key=frequency.get)
    
    return most_frequent

'''
def process_datas(datas,MODEL_NAME):
    results = []

    # 送入多线程任务
    for data in tqdm(datas, desc="Submitting tasks", total=len(datas)):
        problem = data['problem']
        for id,question in enumerate(data['questions']):
            prompt = get_prompt(problem, 
                                question['question'], 
                                question['options'],
                                    )
            #res,res1,res2 = api_retry(MODEL_NAME, prompt),api_retry(MODEL_NAME, prompt),api_retry(MODEL_NAME, prompt)
            res= api_retry(MODEL_NAME, prompt)
            #extract_response,extract_response1,extract_response2 = extract(res),extract(res1),extract(res2)
            extract_response= extract(res)
            #ans = most_frequent_char(extract_response,extract_response1,extract_response2)
            ans = extract_response
            data['questions'][id]['answer'] = ans
            results.append(data) 
    return results
'''

def process_datas(datas,MODEL_NAME):
    results = []
    # 定义线程池 选择16线程
    with ThreadPoolExecutor(max_workers=16) as executor:
        # 这里我们使用future_data 存储每个线程的数据
        future_data = {}
        # 这里的lens记录了调用api的次数，也就是我们每个问题背景下的所有子问题之和。
        lens = 0
        # 送入多线程任务
        # 这里每个data下是一个问题背景，其中包含多个子问题。
        for data in tqdm(datas, desc="Submitting tasks", total=len(datas)):
            problem = data['problem']
            # 这里面我们用enumerate方法每次循环得到问题的序号id和实际的问题。
            for id,question in enumerate(data['questions']):
                prompt = get_prompt(problem, 
                                    question['question'], 
                                    question['options'],
                                    )
                # 这里送入线程池等待处理，使用api_retry，向api_retry传入MODEL_NAME, prompt参数
                future = executor.submit(api_retry, MODEL_NAME, prompt)
                # 每个线程我们存储对应的json问题数据以及问题序号id，这样我们就能定位出执行的是哪个子问题
                future_data[future] = (data,id)
                time.sleep(0.6)  # 控制每0.6秒提交一个任务 防止接口超过并发数
                lens += 1
        # 处理多线程任务
        for future in tqdm(as_completed(future_data), total=lens, desc="Processing tasks"):
            # print('data',data)
            # 取出每个线程中的字典数据及对应的问题id
            data = future_data[future][0]
            problem_id = future_data[future][1]
            try:
                # 获取api运行结果
                res  = future.result()
                # 抽取大语言模型返回结果
                extract_response = extract(res)
                # print('res',extract_response)
                # 装入answer字段
                data['questions'][problem_id][MODEL_NAME] = extract_response
                # 在结果列表中新增数据字典
                results.append(data)
                # print('data',data)
                
            except Exception as e:
                logger.error(f"Failed to process text: {data}. Error: {e}")
    
    return results

def has_complete_answer(questions):
    # 这里假设完整答案的判断逻辑是：每个question都有一个'answer'键
    for question in questions:
        if MODEL_NAME not in question:
            return False
    return True

def filter_problems(data):
    result = []
    problem_set = set()

    for item in data:
        # print('处理的item' ,item)
        problem = item['problem']
        if problem in problem_set:
            # 找到已存在的字典
            for existing_item in result:
                if existing_item['problem'] == problem:
                    # 如果当前字典有完整答案，替换已存在的字典
                    if has_complete_answer(item['questions']):
                        existing_item['questions'] = item['questions']
                        existing_item['id'] = item['id']
                    break
        else:
            # 如果当前字典有完整答案，添加到结果列表
            if has_complete_answer(item['questions']):
                result.append(item)
                problem_set.add(problem)

    return result

def find_missing_ids(dict_list,length):
    # 提取所有序号
    extracted_ids = {int(d['id'][-3:]) for d in dict_list}
    
    # 创建0-500的序号集合
    all_ids = set(range(length))
    
    # 找出缺失的序号
    missing_ids = all_ids - extracted_ids
    
    return sorted(missing_ids)

def format_submit_file(file):
    validated_problem_sets = []
    for data in file:
        questions = data['questions']
        _id = data['id']
        validated_questions = []
        for question in questions:
            validated_questions.append(
                {"answer": question[MODEL_NAME]}
             )
        # 创建一个新的问题集字典，只包含有效的问题
        validated_problem_set = {
            'id': _id,
            'questions': validated_questions
        }
        validated_problem_sets.append(validated_problem_set)
    return validated_problem_sets

def main(ifn, ofn):
    if os.path.exists(ofn):
        pass
    data = []
    # 按行读取数据
    with open(ifn) as reader:
        for line in reader:
            sample = json.loads(line)
            data.append(sample)
    datas = data
    # print(data)
    # 均匀地分成多个数据集
    return_list = process_datas(datas,MODEL_NAME)
    #print(len(return_list))
    print("All tasks finished!")


    return_list1 = filter_problems(return_list)
    sorted_data = sorted(return_list1, key=lambda x: int(str(x['id'])[-3:]))

    # 示例字典列表
    dict_list = sorted_data

    # 找出缺失的序号
    missing_ids = find_missing_ids(dict_list,len(datas))
    print(f"缺失的序号: {missing_ids} 缺失数量: {len(missing_ids)}")

    data  = []
    with open(ifn) as reader:
        for id,line in enumerate(reader):
            if(id in missing_ids):
                sample = json.loads(line)
                for question in sample['questions']:
                    question[MODEL_NAME] = 'A'
                sorted_data.append(sample)
    sorted_data = sorted(sorted_data, key=lambda x: int(str(x['id'])[-3:]))
    with open(ofn, 'w') as writer:
        for sample in sorted_data:
            writer.write(json.dumps(sample, ensure_ascii=False))
            writer.write('\n')
    return sorted_data


In [5]:
def evaluate(data):
    data = data

    pse = 0
    cnt = 0
    tot = 0
    for task in data:
        for question in task['questions']:
            #print(task)
            if MODEL_NAME in question:
                
                tot += 1
                cnt += question[MODEL_NAME] == question['answer']
            else:
                pse += 1

    print(cnt, tot, cnt/tot, pse)

In [ ]:
import run_vllm
import datetime
time.sleep(5)

if __name__ == '__main__':
    filename = "./submit/submit_"+datetime.datetime.now().strftime('%Y%m%d_%H%M%S')
    resultname = "./submit/result_"+datetime.datetime.now().strftime('%Y%m%d_%H%M%S')
    return_list = main('./data/round1_train_data.jsonl', resultname)
    evaluate(return_list)
    submit_file = format_submit_file(return_list)
    with open(filename, 'w') as writer:
        for sample in submit_file:
            writer.write(json.dumps(sample, ensure_ascii=False))
            writer.write('\n')

命令执行失败，退出码：None


/usr/local/lib/python3.10/site-packages/_distutils_hack/__init__.py:55: UserWarning: Reliance on distutils from stdlib is deprecated. Users must rely on setuptools to provide the distutils module. Avoid importing distutils or import setuptools first, and avoid setting SETUPTOOLS_USE_DISTUTILS=stdlib. Register concerns at https://github.com/pypa/setuptools/issues/new?template=distutils-deprecation.yml
  warnings.warn(
2024-09-06 23:42:34.385948: I tensorflow/core/util/port.cc:153] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2024-09-06 23:42:34.396789: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:485] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-09-06 23:42:34.410330: E external/local_xla/xla/stream_executor/cuda/c

INFO 09-06 23:42:38 api_server.py:219] vLLM API server version 0.5.3.post1
INFO 09-06 23:42:38 api_server.py:220] args: Namespace(host=None, port=8000, uvicorn_log_level='info', allow_credentials=False, allowed_origins=['*'], allowed_methods=['*'], allowed_headers=['*'], api_key=None, lora_modules=None, prompt_adapters=None, chat_template=None, response_role='assistant', ssl_keyfile=None, ssl_certfile=None, ssl_ca_certs=None, ssl_cert_reqs=0, root_path=None, middleware=[], model='./model/Meta-Llama-3.1-8B-Instruct-lora', tokenizer=None, skip_tokenizer_init=False, revision=None, code_revision=None, tokenizer_revision=None, tokenizer_mode='auto', trust_remote_code=False, download_dir=None, load_format='auto', dtype='auto', kv_cache_dtype='auto', quantization_param_path=None, max_model_len=4096, guided_decoding_backend='outlines', distributed_executor_backend=None, worker_use_ray=False, pipeline_parallel_size=1, tensor_parallel_size=1, max_parallel_loading_workers=None, ray_workers_use_ns

Submitting tasks:   0%|          | 1/500 [00:02<16:42,  2.01s/it]

INFO 09-06 23:42:39 model_runner.py:680] Starting to load model ./model/Meta-Llama-3.1-8B-Instruct-lora...


...

INFO 09-06 23:50:42 logger.py:36] Received request chat-b84652a1195d484bb82cf49c30c4578c: prompt: '<|begin_of_text|><|start_header_id|>system<|end_header_id|>\n\nCutting Knowledge Date: December 2023\nToday Date: 26 Jul 2024\n\n<|eot_id|><|start_header_id|>user<|end_header_id|>\n\n你是一个逻辑推理专家，擅长解决逻辑推理问题。以下是一个逻辑推理的题目，形式为单项选择题。所有的问题都是（close-world assumption）闭世界假设，即未观测事实都为假。请逐步分析问题并在最后一行输出答案，最后一行的格式为"答案是：A"。题目如下：\n### 题目:\n有一种数学问题涉及将一个给定的整数表示为几个完全平方数的和。考虑以下相关的情况和线索：\n\n1. 这个问题依赖于将整数表示为3个或4个数的平方和。\n2. 对于每个情况，算法会尝试找到一种将该整数分解成少量完全平方数的方式。\n3. 如果找不到合适的数字来满足这种��解，会被认为这是一个无效的计算。\n\n根据以上线索，回答以下选择题：\n### 问题:\n选择题 1：\n数字0可以被表示为几个完全平方数的和（选择可能的解）？\n### 选项:\nA. 2\nB. 3, 4\nC. 4, 5\nD. 5\n### 回答:\n分析：数字0本身可以被视为0的平方，即\\(0^2 = 0\\)。因此，至少可以表示为1个完全平方数的和。但题目要求考虑的是3个或4个数的平方和来表示的情况。对于0，我们可以这样分解：\n- 使用3个数：\\(0^2 + 0^2 + 0^2 = 0\\)\n- 使用4个数：\\(0^2 + 0^2 + 0^2 + 0^2 = 0\\)\n\n这表明0可以按照题目要求以3个或4个完全平方数的和来表示。但选项中没有直接列出“1”作为可能的解，而是从3开始列出。鉴于题目特定条件（考虑3个或4个数的平方和），答案应关注于提供的选项内容而非理论上的最小数量。\n\n因此，根据题目给定的选项和条件：\n- A. 2（不适用，因

Submitting tasks:  51%|█████     | 256/500 [08:08<08:38,  2.13s/it]

INFO 09-06 23:50:45 logger.py:36] Received request chat-099d0582f8574636a9ca01d9180e6bed: prompt: '<|begin_of_text|><|start_header_id|>system<|end_header_id|>\n\nCutting Knowledge Date: December 2023\nToday Date: 26 Jul 2024\n\n<|eot_id|><|start_header_id|>user<|end_header_id|>\n\n你是一个逻辑推理专家，擅长解决逻辑推理问题。以下是一个逻辑推理的题目，形式为单项选择题。所有的问题都是（close-world assumption）闭世界假设，即未观测事实都为假。请逐步分析问题并在最后一行输出答案，最后一行的格式为"答案是：A"。题目如下：\n### 题目:\n有三个人参观了不同的景点，每个人在不同的时间出现在这些景点。以下是已知的信息：\n\n1. person1 在第 2 分钟出现。\n2. person2 在第 5 分钟出现。\n3. person3 在第 10 分钟出现。\n\n他们参观了以下景点并记录了时间：\n- person1 参观了历史博物馆，在第 5 分钟。\n- person2 参观了 Lobnoye mesto，在第 7 分钟。\n- person1 参观了陵墓，在第 9 分钟。\n- person3 参观了喀山大教堂，在第 11 分钟。\n- person2 参观了历史博物馆，在第 12 分钟。\n- person1 参观了喀山大教堂，在第 15 分钟。\n- person3 参观了陵墓，在第 16 分钟。\n- person2 参观了陵墓，在第 18 分钟。\n- person3 参观了喀山大教堂，在第 20 分钟。\n- person2 参观了历史博物馆，在第 22 分钟。\n- person3 参观了陵墓，在第 23 分钟。\n- person2 参观了陵墓，在第 25 分钟。\n- person2 参观了 Lobnoye mesto，在第 26 分钟。\n- person3 参观了历史博物馆，在第 27 分钟。\n- person3 参观了陵墓，在第 28 分钟

Submitting tasks:  51%|█████▏    | 257/500 [08:08<06:51,  1.69s/it]

INFO 09-06 23:50:46 async_llm_engine.py:140] Finished request chat-099d0582f8574636a9ca01d9180e6bed.
INFO:     ::1:60898 - "POST /v1/chat/completions HTTP/1.1" 200 OK
INFO 09-06 23:50:46 logger.py:36] Received request chat-6e6c7d0aeb7b4c4e9f82b44796e6da76: prompt: '<|begin_of_text|><|start_header_id|>system<|end_header_id|>\n\nCutting Knowledge Date: December 2023\nToday Date: 26 Jul 2024\n\n<|eot_id|><|start_header_id|>user<|end_header_id|>\n\n你是一个逻辑推理专家，擅长解决逻辑推理问题。以下是一个逻辑推理的题目，形式为单项选择题。所有的问题都是（close-world assumption）闭世界假设，即未观测事实都为假。请逐步分析问题并在最后一行输出答案，最后一行的格式为"答案是：A"。题目如下：\n### 题目:\n有一组关系定义了谁喜欢谁，并且可以通过这些关系推导出一些新的信息。给定以下已知条件和函数：\n\n1. a 喜欢 b。\n2. b 喜欢 c。\n3. c 喜欢 e。\n4. e 喜欢 a。\n5. e 喜欢 f。\n6. f 喜欢 h。\n7. d 喜欢 i。\n\n请回答以下问题：\n\n### 问题:\n选择题 1：\n列表 [1,2,3,4,5] 中有多少个元��？\nA. 3\nB. 4\nC. 5\nD. 6\n### 回答:\n这个问题实际上与逻辑推理无关，而是一个简单的数学问题。题目中给出的列表是 [1,2,3,4,5]，我们只需要数一下这个列表中有多少个元素。\n\n列表中的元素分别是：\n1. 1\n2. 2\n3. 3\n4. 4\n5. 5\n\n一共有5个元素。\n\n答案是：C. 5\n\n### 题目:\n有一组关系定义了谁喜欢谁，并且可以通过这些关系推导出一些新的信息。给定以下

In [ ]:
import os

# 获取当前工作目录
current_directory = os.getcwd()

# 打印当前工作目录
print("当前工作目录:", current_directory)